# 0.0. Imports

In [7]:
import pandas                      as pd
import numpy                       as np
import seaborn                     as sns
import inflection
import math
import datetime

from boruta                        import BorutaPy
from sklearn.ensemble              import RandomForestRegressor
from sklearn.linear_model          import LinearRegression, Lasso
from sklearn.preprocessing         import RobustScaler, MinMaxScaler, LabelEncoder
from scipy.stats                   import chi2_contingency
from scipy                         import stats  as ss
from matplotlib                    import pyplot as plt
from IPython.display               import Image
from matplotlib                    import gridspec
from IPython.core.display          import HTML
from IPython.core.interactiveshell import InteractiveShell

InteractiveShell.ast_node_interactivity = "all"

## 0.1. Helper functions

In [8]:
def jupyter_settings():
    %matplotlib inline
    %pylab inline
    
    plt.style.use( 'bmh' )
    plt.rcParams['figure.figsize'] = [35, 12]
    plt.rcParams['font.size'] = 24
    
    display( HTML( '<style>.container { width:100% !important; }</style>') )
    pd.options.display.max_columns = None
    pd.options.display.max_rows = None
    pd.set_option( 'display.expand_frame_repr', False )
    
    sns.set()

In [9]:
jupyter_settings()

Populating the interactive namespace from numpy and matplotlib


## 0.2. Loading Data

In [27]:
# load data
df_raw = pd.read_csv('dataset/kc_house_data.csv', low_memory=False) 

# 1.0. Data Preparation

In [25]:
df1 = df_raw.copy()

In [26]:
df1.head()

id             date     price  bedrooms  bathrooms  sqft_living  sqft_lot  floors  waterfront  view  condition  grade  sqft_above  sqft_basement  yr_built  yr_renovated  zipcode      lat     long  sqft_living15  sqft_lot15
0  7129300520  20141013T000000  221900.0         3       1.00         1180      5650     1.0           0     0          3      7        1180              0      1955             0    98178  47.5112 -122.257           1340        5650
1  6414100192  20141209T000000  538000.0         3       2.25         2570      7242     2.0           0     0          3      7        2170            400      1951          1991    98125  47.7210 -122.319           1690        7639
2  5631500400  20150225T000000  180000.0         2       1.00          770     10000     1.0           0     0          3      6         770              0      1933             0    98028  47.7379 -122.233           2720        8062
3  2487200875  20141209T000000  604000.0         4       3.00         1960      5000     1.0           0     0          5      7        1050            910      1965             0    98136  47.5208 -122.393           1360        5000
4  1954400510  20150218T000000  510000.0         3       2.00         1680      8080     1.0           0     0          3      8        1680              0      1987             0    98074  47.6168 -122.045           1800        7503

## 1.1. Data Dimension

In [28]:
# verify number of rows and columns in the dataset

print('Number of rows: {}'.format (df1.shape[0]))
print('Number of Cols: {}'.format (df1.shape[1]))

Number of rows: 21613
Number of Cols: 21


## 1.3. Data types

In [29]:
# change date object to datetime
df1['date'] = pd.to_datetime(df1['date'])

In [30]:
df1.dtypes

id                        int64
date             datetime64[ns]
price                   float64
bedrooms                  int64
bathrooms               float64
sqft_living               int64
sqft_lot                  int64
floors                  float64
waterfront                int64
view                      int64
condition                 int64
grade                     int64
sqft_above                int64
sqft_basement             int64
yr_built                  int64
yr_renovated              int64
zipcode                   int64
lat                     float64
long                    float64
sqft_living15             int64
sqft_lot15                int64
dtype: object

## 1.4. Number of NA

In [31]:
# show sum of NA 
df1.isna().sum()

id               0
date             0
price            0
bedrooms         0
bathrooms        0
sqft_living      0
sqft_lot         0
floors           0
waterfront       0
view             0
condition        0
grade            0
sqft_above       0
sqft_basement    0
yr_built         0
yr_renovated     0
zipcode          0
lat              0
long             0
sqft_living15    0
sqft_lot15       0
dtype: int64

## 1.5. Descriptive Statistics

In [34]:
# Separete numeric and categorical variables
num_atributtes = df1.select_dtypes(include = ['int64', 'float64'])
cat_atributtes = df1.select_dtypes(exclude = ['int64', 'float64', 'datetime64[ns]'])

In [ ]:
# Central Tendency - Mean, Median

#Dispersion - std deviation, min, max, range, skew, kurtosis



In [35]:
num_atributtes

1680        5000
21523  3304300300   579950.0         4       2.75         2460      8643     2.0           0     0          3      9        2460              0      2011             0    98059  47.4828 -122.133           3110        8626
21524  6453550090   861111.0         4       2.50         3650      7090     2.0           0     0          3     10        3650              0      2008             0    98074  47.6060 -122.052           3860        7272
21525  2625069038  1450000.0         4       3.50         4300    108865     2.0           0     0          3     11        4300              0      2014             0    98074  47.6258 -122.005           4650      107498
21526  1760650820   290000.0         3       2.25         1610      3764     2.0           0     0          3      7        1610              0      2012             0    98042  47.3589 -122.083           1610        3825
21527  9578060230   535000.0         4       2.50         2610      4595     2.0           0     0          3      8        2610              0      2008             0    98028  47.7728 -122.235           2440        4588
21528  3416600750   585000.0         3       2.50         1750      1381     3.0           0     0          3      8        1750              0      2008             0    98122  47.6021 -122.294           1940        4800
21529  2487200490   670000.0         3       2.50         3310      5300     2.0           0     2          3      8        2440            870      2008             0    98136  47.5178 -122.389           2140        7500
21530  8964800330  3000000.0         4       3.75         5090     14823     1.0           0     0          3     11        4180            910      2013             0    98004  47.6200 -122.207           3030       12752
21531  5637500082   346000.0         3       2.00         1060      1184     2.0           0     0          3      7         730            330      2006             0    98136  47.5443 -122.385           1270        1601
21532   324069112  1325000.0         4       4.00         4420     16526     2.0           0     0          3     11        4420              0      2013             0    98075  47.5914 -122.027           3510       50447
21533   524059322   999999.0         3       2.50         2100      4097     2.0           0     0          3      9        2100              0      2008             0    98004  47.5983 -122.200           1780        4764
21534   889000025   599000.0         3       1.75         1650      1180     3.0           0     0          3      8        1650              0      2014             0    98105  47.6636 -122.319           1720        1960
21535  2909310100   332000.0         4       2.50         2380      5737     2.0           0     0          3      7        2380              0      2010             0    98023  47.2815 -122.356           2380        5396
21536  8562780180   336750.0         2       2.25         1170      1011     2.0           0     0          3      7        1170              0      2009             0    98027  47.5321 -122.073           1240         750
21537  1043000100   370000.0         4       2.50         2531      6843     2.0           0     0          3      8        2531              0      2013             0    98030  47.3850 -122.189           2604        6238
21538  1865400076   324000.0         3       2.25          998       904     2.0           0     0          3      7         798            200      2007             0    98117  47.6983 -122.367            998        1110
21539  8902000201   338500.0         3       2.25         1333      1470     3.0           0     3          3      7        1333              0      2009             0    98125  47.7058 -122.302           1360        1680
21540   715010530  1881580.0         5       3.50         4410     13000     2.0           0     3          3     10        2920           1490      2014             0    98006  47.5382 -122.111           5790